In [ ]:
import sys
sys.path.append('/home/daylen/xgboost/python-package')

In [ ]:
import sklearn
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import RandomizedSearchCV
from sklearn import metrics
from sklearn import model_selection
from sklearn.utils import shuffle
from sklearn import svm
import numpy as np
import matplotlib.pyplot as plt
import itertools
import pandas
from sklearn_porter import Porter
from sklearn.externals import joblib
import xgboost as xgb
import time
# sudo apt-get install opencv-python
import cv2
%matplotlib inline

In [ ]:
xgb.__path__

In [ ]:
cv2.__version__

## Data Preprocessing


In [ ]:
% ls /mnt/flashblade/daylen/ml_data/lane_change/chessday/*.csv

In [ ]:
FNAME_PREFIX = '/mnt/flashblade/daylen/ml_data/lane_change/chessday/city_highway'

In [ ]:
%%time
train_data = pandas.read_csv(FNAME_PREFIX + '_train.csv')
test_data = pandas.read_csv(FNAME_PREFIX + '_test.csv')

In [ ]:
train_data.shape

In [ ]:
train_data[train_data['agent_front_right_dist_to_right_lane19'] < -4]

In [ ]:

import matplotlib.pyplot as plt
import numpy as np; np.random.seed(1)

bins = np.arange(-10, 4, 0.5)

frq, edges = np.histogram(train_data['agent_front_right_dist_to_right_lane19'], bins)

fig, ax = plt.subplots()
ax.bar(edges[:-1], frq, width=np.diff(edges), ec="k", align="edge")

plt.show()

In [ ]:
train_data['label'].value_counts()
print 'baseline accuracy', float(sum(train_data['label'] == 'IN_LANE')) / train_data.shape[0]

In [ ]:
print 'train straight', sum(train_data['label'] == 'IN_LANE')
print 'train LC', train_data.shape[0] - sum(train_data['label'] == 'IN_LANE')
print 'test straight', sum(test_data['label'] == 'IN_LANE')
print 'test LC', test_data.shape[0] - sum(test_data['label'] == 'IN_LANE')

In [ ]:
def xy_split(samples):
    """
    splits row into x and y
    y can include metadata, it's not just the label
    """
    # TODO magic num
    NUM_FEATURES = 200
    return samples.iloc[:,:NUM_FEATURES], samples.iloc[:,NUM_FEATURES:]

In [ ]:
%%time
xtrain, ytrain = xy_split(train_data)
xtest, ytest = xy_split(test_data)

In [ ]:
# Label encoding
le = sklearn.preprocessing.LabelEncoder()
le.fit(['IN_LANE', 'LEFT', 'RIGHT'])
ytrain_encoded = le.transform(ytrain['label'])
ytest_encoded = le.transform(ytest['label'])

In [ ]:
xtrain_mini, ytrain_mini = xtrain, ytrain
ytrain_mini_encoded = le.transform(ytrain_mini['label'])

# opencv gradient boosted trees

In [ ]:
# evaluation helper functions
import progressbar

def accuracy(x, y):
    x_matrix = x.as_matrix().astype(np.float32)
    correct = 0
    bar = progressbar.ProgressBar()
    
    for i in bar(range(x_matrix.shape[0])):
        pred = gbtrees.predict(x_matrix[i])
        if pred == y[i]:
            correct += 1
    return float(correct) / x_matrix.shape[0]

def predict_all(x):
    x_matrix = x.as_matrix().astype(np.float32)
    preds = []
    bar = progressbar.ProgressBar()
    for i in bar(range(x_matrix.shape[0])):
        pred = gbtrees.predict(x_matrix[i])
        preds.append(pred)
    return preds



In [ ]:
# params

param_grid = sklearn.model_selection.ParameterGrid({
    'loss_function_type': [cv2.GBTREES_DEVIANCE_LOSS],
    'weak_count': [8],
    'shrinkage': [0.1],
    'subsample_portion': [1],
    'max_depth': [6],
    'use_surrogates': [False]
})

In [ ]:
%%time

# train
results = []
print len(param_grid)
for params in list(param_grid):
    start_t = time.time()
    print params
    gbtrees = cv2.GBTrees()
    gbtrees.train(xtrain_mini.as_matrix().astype(np.float32), cv2.CV_ROW_SAMPLE, ytrain_mini_encoded,
                params=params)
    test_acc = accuracy(xtest, ytest_encoded)
    print test_acc
    print 'took', time.time() - start_t, 'sec'
    print ''
    results.append((params, accuracy, time.time() - start_t))

In [ ]:
# save model
gbtrees.save('/home/daylen/ml_models/lane_change_gbt_v3_b3.yaml')

In [ ]:
# load model

gbtrees = cv2.GBTrees()
gbtrees.load('/home/daylen/ml_models/lane_change_gbt_v2_b2.yaml')

In [ ]:
# print accuracy(xtrain, ytrain_encoded)
# print accuracy(xtest, ytest_encoded)

ytestpred = np.array(predict_all(xtest))

In [ ]:
ytestpred

In [ ]:

def predict_all_prob(x):
    x_matrix = x.as_matrix().astype(np.float32)
    all_probs = []
    bar = progressbar.ProgressBar()
    for i in bar(range(x_matrix.shape[0])):
        probs = []
        # TODO(daylen): this assumes the k are in order. Check the OpenCV yaml
        # file to see if this is really the case.
        for k in [0, 1, 2]:
            prob = gbtrees.predict(x_matrix[i], k=k)
            probs.append(np.exp(prob))
        all_probs.append(probs)
    all_probs = np.array(all_probs)
    all_probs /= np.sum(all_probs, axis=1)[:,None]
    return all_probs
ytestpredproba = predict_all_prob(xtest)


In [ ]:
ytestpredproba

In [ ]:
def predict_with_threshold(probs, threshold):
    preds = []
    for row in probs:
        if row[1] > threshold:
            preds.append(1)
        elif row[2] > threshold:
            preds.append(2)
        else:
            preds.append(0)
    return np.array(preds)
ytestpred = predict_with_threshold(ytestpredproba, 0.8)

## xgboost

In [ ]:
# Convert numpy to XGB buffer
dtrain = xgb.DMatrix(xtrain, label=ytrain_encoded)
dtest = xgb.DMatrix(xtest, label=ytest_encoded)
# dtrain.save_binary('/home/daylen/ml_data/xgb_train.buffer')
# dtest.save_binary('/home/daylen/ml_data/xgb_test.buffer')

In [ ]:
# Load XGB buffer
dtrain = xgb.DMatrix('/home/daylen/ml_data/xgb_train.buffer')
dtest = xgb.DMatrix('/home/daylen/ml_data/xgb_test.buffer')

In [ ]:
# Stats
print dtrain.num_row()

In [ ]:
# Just take 1M samples
# dtrain = xgb.DMatrix(xtrain_mini.as_matrix(), label=ytrain_mini_encoded)

In [ ]:
%%time
params = {'tree_method': 'hist',  'objective': 'multi:softmax', 'num_class': 3, 'max_depth': 12, 'eta': 0.1}
evallist = [(dtest, 'test'), (dtrain, 'train')]
print 'Begin training'
bst = xgb.train(params, dtrain, 16, evallist)


In [ ]:
# Save model
bst.save_model('/home/daylen/ml_models/xgb_count_16_depth_12_n_6M_with_junction.model')

In [ ]:
# Load model
bst = xgb.Booster()
bst.load_model('/home/daylen/ml_models/xgb_count_16_depth_12_n_6M_with_junction.model')

In [ ]:
# Predict
ytrainpred = bst.predict(dtrain)
ytestpred = bst.predict(dtest)

## eval

In [ ]:
def plot_confusion_matrix(cm, classes,
                          normalize=False,
                          title='Confusion matrix',
                          cmap=plt.cm.Blues, plotobj=None, in_grid=False):
    """
    This function prints and plots the confusion matrix.
    Normalization can be applied by setting `normalize=True`.
    """
    
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        cm = np.nan_to_num(cm)
        print("Normalized confusion matrix")
    else:
        print('Confusion matrix, without normalization')

    print(cm)
    
    if not plotobj:
        plotobj = plt
    plotobj.imshow(cm, interpolation='nearest', cmap=cmap)
    if not in_grid:
        plotobj.title(title + (' NORMALIZED' if normalize else ''))
    else:
        plotobj.set_title(title + (' NORMALIZED' if normalize else ''))
    if not in_grid:
        plotobj.colorbar()
    tick_marks = np.arange(len(classes))
    if not in_grid:
        plotobj.xticks(tick_marks, classes)
        plotobj.yticks(tick_marks, classes, rotation=90)
    else:
        plotobj.set_xticks(tick_marks, minor=False)
        plotobj.set_yticks(tick_marks, minor=False)
        plotobj.set_xticklabels(classes)
        plotobj.set_yticklabels(classes, rotation=90)


    thresh = cm.max() / 2.
    for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
        plotobj.text(j, i, '%.4f' % cm[i, j],
                 horizontalalignment="center",
                 color="white" if cm[i, j] > thresh else "black")
    if not in_grid:
        plotobj.ylabel('True label')
        plotobj.xlabel('Predicted label')
    else:
        plotobj.set_ylabel('True label')
        plotobj.set_xlabel('Predicted label')

In [ ]:
# metrics
# for train and test...
# percent of time that we predict IN_LANE if label is IN_LANE
# percent of time we predict LEFT or RIGHT if label is LEFT or RIGHT at 2 sec, 1 sec, 0.5 sec before LC

def get_lane_changes_with_t_minus(t, y):
    return y.index[((y['label'] == 'RIGHT') | (y['label'] == 'LEFT')) & (y['time_until_center_crosses'] > t - 0.01) & (y['time_until_center_crosses'] < t + 0.01)]

def print_metrics(ypred, y):
    label_names = ["IN_LANE", "LEFT", "RIGHT"]
    cnf = metrics.confusion_matrix(y['label'], ypred, labels=label_names)
    plt.figure()
    plot_confusion_matrix(cnf, label_names, True, title='All test set samples')
    print 'IN_LANE recall', float(cnf[0,0]) / (np.sum(cnf[0]))
    
    times = [2.0, 1.0]
    for time in times:
        print 'At t=', time
        idxs = get_lane_changes_with_t_minus(time, y)
        cnf = metrics.confusion_matrix(y.ix[idxs]['label'], np.take(ypred, idxs), labels=label_names)
        plt.figure()
        plot_confusion_matrix(cnf, label_names, normalize=True, title=str(time) + ' sec before LC')
        
print_metrics(le.inverse_transform(ytestpred.astype(int)), ytest)
# print_metrics(le.inverse_transform(ytestpred), ytest)

#print_metrics(ytestpred, ytest)

In [ ]:
# Failure cases
def failure_to_predict_lane_change(ypred, y):
    idxs = get_lane_changes_with_t_minus(0.2, y)
    for i in idxs:
        if ypred[i] != y.ix[i]['label']:
            print i, 'pred', ypred[i], 'label', y.ix[i]['label'], y.ix[i]['event_key']

def failure_to_predict_in_lane(ypred, y):
    for i in range(len(ypred)):
        if y['label'][i] == 'IN_LANE' and ypred[i] != 'IN_LANE':
            print i, 'pred', ypred[i], 'label', y.ix[i]['label'], y.ix[i]['event_key']
# failure_to_predict_lane_change(le.inverse_transform(ytestpred.astype(int)), ytest)
failure_to_predict_in_lane(le.inverse_transform(ytestpred.astype(int)), ytest)

metrics todo:
- median "warning time" before center crossed (p2)
- median "warning time" before edge crossed (p1)
- median "warning time" before following (p0)
- median edge distance before predicted

examples:
- success cases
- failure cases

In [ ]:
print 'Number of events'
hashes = test_data['event_key']
unique_hashes = np.unique(hashes)

i = 0
for h in unique_hashes:
    rows = test_data[test_data['event_key'] == h]
    event_labels = rows['label']
    if 'LEFT' not in event_labels.tolist() and 'RIGHT' not in event_labels.tolist():
        continue
    # Determine when following would have followed
    print rows['']
    # Determine when we would have predicted
    
    
    i += 1
    if i == 5:
        break

## P/R curves
We want to transform the 3-class data into a 2-class problem fixed at a particular time before the lane change (1 second). This way the curve is very easy to interpret.

In [ ]:
from sklearn.preprocessing import label_binarize
ytest_binarized = label_binarize(ytest['label'], classes=['IN_LANE', 'LEFT', 'RIGHT'])

In [ ]:
from sklearn.metrics import precision_recall_curve
from sklearn.metrics import average_precision_score
n_classes = 3
# For each class
precision = dict()
recall = dict()
average_precision = dict()
for i in range(n_classes):
    precision[i], recall[i], _ = precision_recall_curve(ytest_binarized[:, i],
                                                        ytestpredproba[:, i])
    average_precision[i] = average_precision_score(ytest_binarized[:, i], ytestpredproba[:, i])

# A "micro-average": quantifying score on all classes jointly
precision["micro"], recall["micro"], _ = precision_recall_curve(ytest_binarized.ravel(),
    ytestpredproba.ravel())
average_precision["micro"] = average_precision_score(ytest_binarized, ytestpredproba,
                                                     average="micro")
print('Average precision score, micro-averaged over all classes: {0:0.2f}'
      .format(average_precision["micro"]))

In [ ]:
from itertools import cycle
# setup plot details
colors = cycle(['navy', 'turquoise', 'darkorange', 'cornflowerblue', 'teal'])

plt.figure(figsize=(7, 8))
f_scores = np.linspace(0.2, 0.8, num=4)
lines = []
labels = []
for f_score in f_scores:
    x = np.linspace(0.01, 1)
    y = f_score * x / (2 * x - f_score)
    l, = plt.plot(x[y >= 0], y[y >= 0], color='gray', alpha=0.2)
    plt.annotate('f1={0:0.1f}'.format(f_score), xy=(0.9, y[45] + 0.02))

lines.append(l)
labels.append('iso-f1 curves')
l, = plt.plot(recall["micro"], precision["micro"], color='gold', lw=2)
lines.append(l)
labels.append('micro-average Precision-recall (area = {0:0.2f})'
              ''.format(average_precision["micro"]))

for i, color in zip(range(n_classes), colors):
    l, = plt.plot(recall[i], precision[i], color=color, lw=2)
    lines.append(l)
    labels.append('Precision-recall for class {0} (area = {1:0.2f})'
                  ''.format(i, average_precision[i]))

fig = plt.gcf()
fig.subplots_adjust(bottom=0.25)
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.05])
plt.xlabel('Recall')
plt.ylabel('Precision')
plt.title('Extension of Precision-Recall curve to multi-class')
plt.legend(lines, labels, loc=(0, -.38), prop=dict(size=14))


plt.show()